<a href="https://colab.research.google.com/github/imarab1/-Stock-Market-Sentiment-Analysis-Using-Python-Machine-Learning/blob/master/Stock_Market_Sentiment_Analysis_Using_Python_%26_Machine_Learning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install vaderSentiment

     |████████████████████████████████| 133kB 7.8MB/s 


In [ ]:
import pandas as pd
import numpy as np
from textblob import TextBlob
import re
import nltk
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

In [ ]:
from google.colab import files
files.upload()

Saving datasets_129_792900_upload_DJIA_table.csv to datasets_129_792900_upload_DJIA_table (2).csv
Saving 129_792900_compressed_Combined_News_DJIA.csv.zip to 129_792900_compressed_Combined_News_DJIA.csv (2).zip


{'129_792900_compressed_Combined_News_DJIA.csv.zip': b'PK\x03\x04-\x00\x00\x00\x08\x00\xdc\x92mOS\xec7\x03\xff\xff\xff\xff\xff\xff\xff\xff\x16\x00\x14\x00Combined_News_DJIA.csv\x01\x00\x10\x00\xde\xb7U\x00\x00\x00\x00\x00a\x96$\x00\x00\x00\x00\x00\xb4\xbdks\x1bI\xb2%\xf8}\xcd\xf6?Dq\xbb\x07UwA\xb6\xa8\x92T%\x96\x8diAR\x94X\x12\x1f#P\xd2\xd6\xed\xdbf\x13@\x06\x80,&2Q\xf9 \x04Y\xff\xf8\xf5s\xdc#2\xc1R\xcf\xec\x9d\xb5\xed\xdbW-\x91@>"<\xdc\x8f\xbb\x1fw?\xf7m\x18\xbf\xf7\xb3P\x8c\xef\xaa\xcd1\xfex\x8a?~\xc4\x1f\xcf\xf0\xc7s\xfc\xf1\x02\x7f\xfc\x84?~\xc6\x1f/\xf9\xe1\'\xfc\x93\xdf9\xe6\x97\x8e\xf9\xadc~\xed\x98\xdf;\xe6\x17\x8f\xf9\xcdc~\xf5\x98\xdf}\xca\xef>\xd5\xfb\xf1\xbbO\xf9\xdd\xa7\xfc\xee\xd3\xe7\xff\xfb\xff\xf6\xf4\xc9\x93\x9f\x0f\xf9\xdf\xf1\x93\xf1\xc1\xec\xe0\xe0M\xa8\xeae\xee\xdd(\xab\xb6e\xe3\xdam\xe5>tM\x93\xfb\xd2m}\xbd)|\x19\x9a\x91\xf3\x8d\x9bW]\xd9\xd6yh\xdc\xbaz\x08\xae\xad\xdc\xac\xce\xcb{W-\xf0\xc1\x83\x83\x83\xf1lt\xfa\xe1\xf5\xe4\xdd\xe5\xf5\x9b\x13w\xd55+_\xd7~\xc1\x

In [ ]:
df1 = pd.read_csv('datasets_129_792900_upload_DJIA_table.csv')
df2 = pd.read_csv('129_792900_compressed_Combined_News_DJIA.csv.zip')

In [ ]:
df1.head(3)

Date          Open  ...     Volume     Adj Close
0  2016-07-01  17924.240234  ...   82160000  17949.369141
1  2016-06-30  17712.759766  ...  133030000  17929.990234
2  2016-06-29  17456.019531  ...  106380000  17694.679688

[3 rows x 7 columns]

In [ ]:
df2.head(3)

Date  ...                                              Top25
0  2008-08-08  ...           b"No Help for Mexico's Kidnapping Surge"
1  2008-08-11  ...  b"So this is what it's come to: trading sex fo...
2  2008-08-12  ...  b"BBC NEWS | Asia-Pacific | Extinction 'by man...

[3 rows x 27 columns]

In [ ]:
merge = df1.merge(df2, how='inner', on='Date', left_index = True)
merge.head(3)

Date  ...                                              Top25
1988  2016-07-01  ...  Ozone layer hole seems to be healing - US &amp...
1987  2016-06-30  ...  Law Enforcement Sources: Gun Used in Paris Ter...
1986  2016-06-29  ...  Tiny New Zealand town with 'too many jobs' lau...

[3 rows x 33 columns]

In [ ]:
headlines = []
for row in range(0,len(merge.index)):
    headlines.append(' '.join(str(x) for x in merge.iloc[row,2:27]))

In [ ]:
clean_headlines = []
for i in range(0, len(headlines)):
  clean_headlines.append(re.sub("b[(')]+", '', headlines[i] ))
  clean_headlines[i] = re.sub('b[(")]+', '', clean_headlines[i] )
  clean_headlines[i] = re.sub("\'", '', clean_headlines[i] )

In [ ]:

merge['Combined_News'] = clean_headlines

In [ ]:
def getSubjectivity(text):
  return TextBlob(text).sentiment.subjectivity
  
def getPolarity(text):
  return  TextBlob(text).sentiment.polarity

In [ ]:
merge['Subjectivity'] =merge['Combined_News'].apply(getSubjectivity)
merge['Polarity'] =merge['Combined_News'].apply(getPolarity)

In [ ]:
def getSIA(text):
  sia = SentimentIntensityAnalyzer()
  sentiment = sia.polarity_scores(text)
  return sentiment

In [ ]:

compound = []
neg = []
neu = []
pos = []
SIA = 0
for i in range(0, len(merge['Combined_News'])):
  SIA = getSIA(merge['Combined_News'][i])
  compound.append(SIA['compound'])
  neg.append(SIA['neg'])
  neu.append(SIA['neu'])
  pos.append(SIA['pos'])

In [ ]:
merge['Compound'] =compound
merge['Negative'] =neg
merge['Neutral'] =neu
merge['Positive'] = pos

In [ ]:
keep_columns = [ 'Open',  'High', 'Low',    'Volume', 'Subjectivity', 'Polarity', 'Compound', 'Negative', 'Neutral' ,'Positive',  'Label' ]
df = merge[keep_columns]
df

Open          High           Low  ...  Neutral  Positive  Label
1988  17924.240234  18002.380859  17916.910156  ...    0.759     0.042      1
1987  17712.759766  17930.609375  17711.800781  ...    0.752     0.087      1
1986  17456.019531  17704.509766  17456.019531  ...    0.761     0.058      1
1985  17190.509766  17409.720703  17190.509766  ...    0.805     0.064      1
1984  17355.210938  17355.210938  17063.080078  ...    0.738     0.085      0
...            ...           ...           ...  ...      ...       ...    ...
4     11532.070312  11718.280273  11450.889648  ...    0.749     0.094      1
3     11632.809570  11633.780273  11453.339844  ...    0.785     0.098      0
2     11781.700195  11782.349609  11601.519531  ...    0.719     0.080      0
1     11729.669922  11867.110352  11675.530273  ...    0.731     0.087      1
0     11432.089844  11759.959961  11388.040039  ...    0.760     0.069      0

[1989 rows x 11 columns]

In [ ]:
X = df
X = np.array(X.drop(['Label'], 1))

y = np.array(df['Label'])

In [ ]:

x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state = 0)

In [ ]:
model = LinearDiscriminantAnalysis().fit(x_train, y_train)

In [ ]:

predictions = model.predict(x_test)
predictions

array([0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1,
       1, 0, 0, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1,
       1, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0, 1, 0,
       0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1,
       1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 0, 1,
       0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0,
       1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 0, 0, 1,
       1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1,
       0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1,
       1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1,
       1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0,
       0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1,
       1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 1,
       0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1,

In [ ]:
print( classification_report(y_test, predictions) )

              precision    recall  f1-score   support

           0       0.88      0.81      0.85       187
           1       0.85      0.91      0.87       211

    accuracy                           0.86       398
   macro avg       0.86      0.86      0.86       398
weighted avg       0.86      0.86      0.86       398

